<a href="https://colab.research.google.com/github/awaab/FraudDetection/blob/main/credit_train_tf.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This notebook follows the tutorial: https://www.tensorflow.org/tutorials/structured_data/imbalanced_data

In [139]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

import tensorflow as tf
from tensorflow import keras

import os
import tempfile

import sklearn
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler

In [140]:
df = pd.read_csv('/content/drive/MyDrive/kaggle/creditcard.csv')
df

Time         V1         V2  ...       V28  Amount  Class
0            0.0  -1.359807  -0.072781  ... -0.021053  149.62      0
1            0.0   1.191857   0.266151  ...  0.014724    2.69      0
2            1.0  -1.358354  -1.340163  ... -0.059752  378.66      0
3            1.0  -0.966272  -0.185226  ...  0.061458  123.50      0
4            2.0  -1.158233   0.877737  ...  0.215153   69.99      0
...          ...        ...        ...  ...       ...     ...    ...
284802  172786.0 -11.881118  10.071785  ...  0.823731    0.77      0
284803  172787.0  -0.732789  -0.055080  ... -0.053527   24.79      0
284804  172788.0   1.919565  -0.301254  ... -0.026561   67.88      0
284805  172788.0  -0.240440   0.530483  ...  0.104533   10.00      0
284806  172792.0  -0.533413  -0.189733  ...  0.013649  217.00      0

[284807 rows x 31 columns]

In [141]:
eps = 0.001
df['log_Ammount'] = np.log(df.pop('Amount')+eps)
#df['Time_round_24']  =df.pop('Time') % (24 * 60 * 60)
df.pop('Time')

0              0.0
1              0.0
2              1.0
3              1.0
4              2.0
            ...   
284802    172786.0
284803    172787.0
284804    172788.0
284805    172788.0
284806    172792.0
Name: Time, Length: 284807, dtype: float64

In [142]:
pos = sum(df["Class"] == 1)
neg = sum(df["Class"] == 0)

In [143]:
scaler = StandardScaler()
y = df["Class"].values
df.pop("Class")
X = scaler.fit_transform(df.values)

In [144]:
X = np.clip(X, -5, 5)

In [145]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=0.2)

In [146]:
X_train.shape, y_train.shape

((182276, 29), (182276,))

In [147]:
METRICS = [
      keras.metrics.TruePositives(name='tp'),
      keras.metrics.FalsePositives(name='fp'),
      keras.metrics.TrueNegatives(name='tn'),
      keras.metrics.FalseNegatives(name='fn'), 
      keras.metrics.BinaryAccuracy(name='accuracy'),
      keras.metrics.Precision(name='precision'),
      keras.metrics.Recall(name='recall'),
      keras.metrics.AUC(name='auc'),
      keras.metrics.AUC(name='prc', curve='PR'), # precision-recall curve
]

In [148]:
def make_model(metrics=METRICS, output_bias=None, input_shape=X_train.shape[1],learning_rate=1e-3):
  if output_bias is not None:
    output_bias = tf.keras.initializers.Constant(output_bias)
    
  model = keras.Sequential([
          keras.layers.Dense(
          16, activation='relu',
          input_shape=(input_shape,)),
          keras.layers.Dropout(0.5),
          keras.layers.Dense(1, activation='sigmoid',bias_initializer=output_bias),
          ])

  model.compile(
      optimizer=keras.optimizers.Adam(learning_rate),
      loss=keras.losses.BinaryCrossentropy(),
      metrics=metrics)

  return model

In [149]:
EPOCHS = 100
BATCH_SIZE = 2048

early_stopping = tf.keras.callbacks.EarlyStopping(
    monitor='val_prc', 
    verbose=1,
    patience=10,
    mode='max',
    restore_best_weights=True)

In [150]:
model = make_model()
model.summary()

Model: "sequential_23"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_46 (Dense)             (None, 16)                480       
_________________________________________________________________
dropout_23 (Dropout)         (None, 16)                0         
_________________________________________________________________
dense_47 (Dense)             (None, 1)                 17        
Total params: 497
Trainable params: 497
Non-trainable params: 0
_________________________________________________________________


In [205]:
def get_results(X=X_train,y=y_train,model=model):
  results = model.evaluate(X, y, batch_size=BATCH_SIZE, verbose=0)
  res = {"loss": results[0]}
  for metric, result in zip(METRICS,results[1:]):
    res[metric.name]= result
  return res

In [152]:
get_results(model=model)

{'accuracy': 0.01383616030216217,
 'auc': 0.15076373517513275,
 'fn': 116.0,
 'fp': 179638.0,
 'loss': 2.022775411605835,
 'prc': 0.000926185748539865,
 'precision': 0.0010621200781315565,
 'recall': 0.6221498250961304,
 'tn': 2331.0,
 'tp': 191.0}

In [153]:

# initialize to reflect imbalance in data, to minimize initial loss
initial_bias = np.log([pos/neg])
model = make_model(output_bias=initial_bias)

In [154]:
get_results(model=model)

{'accuracy': 0.5060649514198303,
 'auc': 0.44292235374450684,
 'fn': 423.0,
 'fp': 179642.0,
 'loss': 0.0127454474568367,
 'prc': 0.0013811460230499506,
 'precision': 0.0010620964458212256,
 'recall': 0.3110749125480652,
 'tn': 184296.0,
 'tp': 191.0}

In [155]:
# save weights to make a fair comparison between models and different hyperparameters
initial_weights = os.path.join(tempfile.mkdtemp(), 'initial_weights')
model.save_weights(initial_weights)

In [156]:
model = make_model()
model.load_weights(initial_weights)
model.layers[-1].bias.assign([0.0])
zero_bias_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=20,
    validation_data=(X_val, y_val), 
    verbose=0)

model = make_model()
model.load_weights(initial_weights)
careful_bias_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=20,
    validation_data=(X_val, y_val), 
    verbose=0)

In [ ]:
get_results(model=model)

In [157]:
def plot_loss(histories, names):
  # Use a log scale on y-axis to show the wide range of values.
  fig = go.Figure()
  for history, name in zip(histories,names):
    fig.add_trace(go.Scatter(x=history.epoch, y=np.log(history.history['loss']),
                        mode='lines',
                        name=name))
  fig.show()

In [158]:
def plot_metrics(history):
  metrics = ['loss', 'prc', 'precision', 'recall']
  
  for metric in metrics:
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history[metric],
                        mode='lines',
                        name="train"))
    fig.add_trace(go.Scatter(x=history.epoch, y=history.history[f"val_{metric}"],
                        mode='lines',
                        name="val"))
    fig.update_layout(title=metric)
    fig.show()

In [159]:
plot_loss([careful_bias_history,zero_bias_history],["careful_bias","zero_bias"])

In [160]:
model = make_model()
model.load_weights(initial_weights)
baseline_history = model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=EPOCHS,
    callbacks=[early_stopping],
    validation_data=(X_val, y_val))

Epoch 1/100
90/90 [==============================] - 3s 16ms/step - loss: 0.0112 - tp: 105.0000 - fp: 82.0000 - tn: 227372.0000 - fn: 286.0000 - accuracy: 0.9984 - precision: 0.5615 - recall: 0.2685 - auc: 0.8379 - prc: 0.2933 - val_loss: 0.0064 - val_tp: 27.0000 - val_fp: 8.0000 - val_tn: 45477.0000 - val_fn: 57.0000 - val_accuracy: 0.9986 - val_precision: 0.7714 - val_recall: 0.3214 - val_auc: 0.9086 - val_prc: 0.6438
Epoch 2/100
90/90 [==============================] - 0s 5ms/step - loss: 0.0069 - tp: 123.0000 - fp: 37.0000 - tn: 181932.0000 - fn: 184.0000 - accuracy: 0.9988 - precision: 0.7688 - recall: 0.4007 - auc: 0.8956 - prc: 0.5170 - val_loss: 0.0051 - val_tp: 48.0000 - val_fp: 10.0000 - val_tn: 45475.0000 - val_fn: 36.0000 - val_accuracy: 0.9990 - val_precision: 0.8276 - val_recall: 0.5714 - val_auc: 0.9101 - val_prc: 0.6607
Epoch 3/100
90/90 [==============================] - 0s 5ms/step - loss: 0.0055 - tp: 164.0000 - fp: 28.0000 - tn: 181941.0000 - fn: 143.0000 - accuracy

In [ ]:
get_results(model=model)

In [161]:
plot_metrics(baseline_history)

In [164]:
get_results(X_test,y_test,model=model)

{'accuracy': 0.9993680119514465,
 'auc': 0.9054792523384094,
 'fn': 29.0,
 'fp': 7.0,
 'loss': 0.00355759309604764,
 'prc': 0.7781887650489807,
 'precision': 0.9113923907279968,
 'recall': 0.7128713130950928,
 'tn': 56854.0,
 'tp': 72.0}

In [202]:
def fig_add_roc(name, labels, predictions, fig):
  fp, tp, thresh = sklearn.metrics.roc_curve(labels, predictions)
  assert len(thresh) == len(tp)
  fig.add_trace(go.Scatter(x=100*fp, y=100*tp,
                        mode="lines+markers",#+text",
                        text=thresh,
                        name=name,
                        marker=dict(
                          size=2,
                        )
  )
  )
  fig.update_layout(
      xaxis_title="False positives [%]",
      yaxis_title="True positives [%]"

  )
def plot_roc(name_lis, labels_lis, pred_lis):
  fig = go.Figure()
  for name, labels, predictions in zip(name_lis, labels_lis, pred_lis):
    fig_add_roc(name, labels, predictions, fig)
  fig.update_layout(
      yaxis_range=[70,100],
      xaxis_range=[0,30],
  )
  fig.show()

In [168]:
train_predictions_baseline = model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_baseline = model.predict(X_test, batch_size=BATCH_SIZE)

In [203]:
plot_roc(["Train","Test"],[y_train,y_test],[train_predictions_baseline,test_predictions_baseline])

### Weighed classes



In [170]:
# Scaling by total/2 helps keep the loss to a similar magnitude.
# The sum of the weights of all examples stays the same.
total = neg + pos
weight_for_0 = (1 / neg) * (total / 2.0)
weight_for_1 = (1 / pos) * (total / 2.0)

class_weight = {0: weight_for_0, 1: weight_for_1}

print('Weight for class 0: {:.2f}'.format(weight_for_0))
print('Weight for class 1: {:.2f}'.format(weight_for_1))

Weight for class 0: 0.50
Weight for class 1: 289.44


In [171]:
weighted_model = make_model()
weighted_model.load_weights(initial_weights)

weighted_history = weighted_model.fit(
    X_train,
    y_train,
    batch_size=BATCH_SIZE,
    epochs=EPOCHS,
    callbacks=[early_stopping],
    validation_data=(X_val, y_val),
    # The class weights go here
    class_weight=class_weight)

Epoch 1/100
90/90 [==============================] - 4s 19ms/step - loss: 1.6537 - tp: 313.0000 - fp: 378.0000 - tn: 363560.0000 - fn: 301.0000 - accuracy: 0.9981 - precision: 0.4530 - recall: 0.5098 - auc: 0.8764 - prc: 0.4245 - val_loss: 0.0098 - val_tp: 55.0000 - val_fp: 14.0000 - val_tn: 45471.0000 - val_fn: 29.0000 - val_accuracy: 0.9991 - val_precision: 0.7971 - val_recall: 0.6548 - val_auc: 0.9484 - val_prc: 0.5730
Epoch 2/100
90/90 [==============================] - 1s 6ms/step - loss: 0.6116 - tp: 200.0000 - fp: 796.0000 - tn: 181173.0000 - fn: 107.0000 - accuracy: 0.9950 - precision: 0.2008 - recall: 0.6515 - auc: 0.9192 - prc: 0.4057 - val_loss: 0.0140 - val_tp: 67.0000 - val_fp: 32.0000 - val_tn: 45453.0000 - val_fn: 17.0000 - val_accuracy: 0.9989 - val_precision: 0.6768 - val_recall: 0.7976 - val_auc: 0.9642 - val_prc: 0.6812
Epoch 3/100
90/90 [==============================] - 1s 7ms/step - loss: 0.4666 - tp: 236.0000 - fp: 1314.0000 - tn: 180655.0000 - fn: 71.0000 - accu

In [206]:
get_results(X_test,y_test,model=weighted_model)

{'accuracy': 0.9958041906356812,
 'auc': 0.9575452208518982,
 'fn': 20.0,
 'fp': 219.0,
 'loss': 0.03039718233048916,
 'prc': 0.708349347114563,
 'precision': 0.27000001072883606,
 'recall': 0.801980197429657,
 'tn': 56642.0,
 'tp': 81.0}

### Oversampling the minority class

In [207]:
y_equal_1 = y_train==1
pos_X = X_train[y_equal_1]
neg_X = X_train[~y_equal_1]

pos_y = y_train[y_equal_1]
neg_y = y_train[~y_equal_1]

ids = np.arange(len(pos_X))
choices = np.random.choice(ids, len(neg_X))

res_pos_X = pos_X[choices]
res_pos_y = pos_y[choices]

res_pos_X.shape

(181969, 29)

In [208]:
resampled_X = np.concatenate([res_pos_X, neg_X], axis=0)
resampled_y = np.concatenate([res_pos_y, neg_y], axis=0)

order = np.arange(len(resampled_y))
np.random.shuffle(order)
resampled_X = resampled_X[order]
resampled_y = resampled_y[order]

resampled_X.shape


(363938, 29)

In [223]:
resampled_model = make_model()
resampled_model.load_weights(initial_weights)

# Reset the bias to zero, since this dataset is balanced.
output_layer = resampled_model.layers[-1] 
output_layer.bias.assign([0])

resampled_history = resampled_model.fit(
    resampled_X,
    resampled_y,
    steps_per_epoch=20,
    epochs=EPOCHS,
    #callbacks=[early_stopping],
    validation_data=(X_val,y_val))


Epoch 1/100
20/20 [==============================] - 5s 157ms/step - loss: 0.7411 - tp: 140375.0000 - fp: 112467.0000 - tn: 104923.0000 - fn: 41661.0000 - accuracy: 0.6141 - precision: 0.5552 - recall: 0.7711 - auc: 0.7474 - prc: 0.7586 - val_loss: 0.8877 - val_tp: 82.0000 - val_fp: 29481.0000 - val_tn: 16004.0000 - val_fn: 2.0000 - val_accuracy: 0.3530 - val_precision: 0.0028 - val_recall: 0.9762 - val_auc: 0.9209 - val_prc: 0.3156
Epoch 2/100
20/20 [==============================] - 3s 148ms/step - loss: 0.5859 - tp: 159632.0000 - fp: 102972.0000 - tn: 78997.0000 - fn: 22337.0000 - accuracy: 0.6557 - precision: 0.6079 - recall: 0.8772 - auc: 0.8372 - prc: 0.8761 - val_loss: 0.7751 - val_tp: 81.0000 - val_fp: 24219.0000 - val_tn: 21266.0000 - val_fn: 3.0000 - val_accuracy: 0.4685 - val_precision: 0.0033 - val_recall: 0.9643 - val_auc: 0.9476 - val_prc: 0.5287
Epoch 3/100
20/20 [==============================] - 3s 136ms/step - loss: 0.5037 - tp: 164066.0000 - fp: 89799.0000 - tn: 9217

In [224]:
plot_metrics(resampled_history)

In [225]:
get_results(X_test,y_test,model=resampled_model)

{'accuracy': 0.9876233339309692,
 'auc': 0.966385543346405,
 'fn': 17.0,
 'fp': 688.0,
 'loss': 0.043823644518852234,
 'prc': 0.6672933101654053,
 'precision': 0.10880828648805618,
 'recall': 0.8316831588745117,
 'tn': 56173.0,
 'tp': 84.0}

In [220]:
train_predictions_weighted = weighted_model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_weighted = weighted_model.predict(X_test, batch_size=BATCH_SIZE)
train_predictions_resampled = resampled_model.predict(X_train, batch_size=BATCH_SIZE)
test_predictions_resampled = resampled_model.predict(X_test, batch_size=BATCH_SIZE)

In [221]:
plot_roc(["Train_baseline","Test_baseline","Train_weiged",'Test_weighed','Train_resampled','Test_resampled'],
         [y_train,y_test]*3,
         [train_predictions_baseline,test_predictions_baseline,train_predictions_weighted,test_predictions_weighted,train_predictions_resampled,test_predictions_resampled])

[1, 2, 1, 2]